# Global settings

In [1]:
%matplotlib inline

#%load_ext autoreload  # Autoreload has a bug : when you modify function in source code and run again, python kernel hangs :(
#%autoreload 2

import datetime as dt

import sys, importlib

from functions import *
importlib.reload(sys.modules['functions'])

import pandas as pd

pd.set_option('display.max_rows', 200)
pd.set_option('display.max_columns', 200)

import datetime as dt

import os
import zipfile
import urllib

import matplotlib.pyplot as plt
import pandas as pd
import numpy as np   
  
import plotly as py
import plotly.graph_objects as go
import ipywidgets as widgets

import qgrid

import glob

from pandas.plotting import scatter_matrix

from sklearn.model_selection import StratifiedShuffleSplit

from sklearn.model_selection import GridSearchCV

from sklearn.manifold import TSNE
from sklearn.manifold import LocallyLinearEmbedding
from sklearn.manifold import Isomap

from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
from sklearn.metrics import pairwise_distances
from sklearn.cluster import AgglomerativeClustering
from scipy.stats import entropy

from sklearn.feature_selection import RFE

from sklearn.tree import DecisionTreeClassifier
from sklearn import tree


import nltk
import codecs

#from nltk.corpus.reader.api import CorpusReader
#from nltk.corpus.reader.api import CategorizedCorpusReader

from nltk import pos_tag, sent_tokenize, wordpunct_tokenize

import pandas_profiling

from bs4 import BeautifulSoup

DATA_PATH = os.path.join("datasets", "stackexchange")
#DATA_PATH = os.path.join(DATA_PATH, "out")

#DATA_PATH_FILE_INPUT = os.path.join(DATA_PATH, "QueryResults_20190101-20200620.csv")
#DATA_PATH_FILE_INPUT = os.path.join(DATA_PATH, "QueryResults 20200301-20200620_1.csv")

DATA_PATH_FILE = os.path.join(DATA_PATH, "*.csv")
ALL_FILES_LIST = glob.glob(DATA_PATH_FILE)

ALL_FEATURES = []

MODEL_CLIENT_FEATURES = ['TotalPricePerMonth', 'DescriptionNormalized', 'HasEverCancelled', 'BoughtTopValueProduct' ]


plt.rcParams["figure.figsize"] = [16,9] # Taille par défaut des figures de matplotlib

import seaborn as sns
from seaborn import boxplot
sns.set()

#import common_functions

####### Paramètres pour sauver et restaurer les modèles :
import pickle
####### Paramètres à changer par l'utilisateur selon son besoin :

'''
RECOMPUTE_GRIDSEARCH = True  # CAUTION : computation is several hours long
SAVE_GRID_RESULTS = False # If True : grid results object will be saved to pickle files that have GRIDSEARCH_FILE_PREFIX
LOAD_GRID_RESULTS = False # If True : grid results object will be loaded from pickle files that have GRIDSEARCH_FILE_PREFIX
                          # Grid search results are loaded with full samples (SAMPLED_DATA must be False)
'''


RECOMPUTE_GRIDSEARCH = False  # CAUTION : computation is several hours long
SAVE_GRID_RESULTS = False # If True : grid results object will be saved to pickle files that have GRIDSEARCH_FILE_PREFIX
LOAD_GRID_RESULTS = True # If True : grid results object will be loaded from pickle files that have GRIDSEARCH_FILE_PREFIX

#GRIDSEARCH_CSV_FILE = 'grid_search_results.csv'

GRIDSEARCH_FILE_PREFIX = 'grid_search_results_'

EXECUTE_INTERMEDIATE_MODELS = True # If True: every intermediate model (which results are manually analyzed in the notebook) will be executed


# Necessary for predictors used in the notebook :
from sklearn.linear_model import LinearRegression
from sklearn.compose import TransformedTargetRegressor
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error

from sklearn.preprocessing import PolynomialFeatures

### For progress bar :
from tqdm import tqdm_notebook as tqdm

# Statsmodel : 
import statsmodels.formula.api as smf

import statsmodels.api as sm
from scipy import stats

SAVE_API_MODEL = True # If True : API model ill be saved
API_MODEL_PICKLE_FILE = 'API_model_PJ6.pickle'


/home/francois/anaconda3/lib/python3.7/site-packages/statsmodels/tools/_testing.py:19: FutureWarning:

pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.



# Doc2vec settings

In [27]:
DOC2VEC_TRAINING_SAVE_FILE = 'doc2vec_model'
#doc2vec_fname = get_tmpfile(DOC2VEC_TRAINING_SAVE_FILE)

from gensim.models.doc2vec import TaggedDocument, Doc2Vec
from gensim.parsing.preprocessing import remove_stopwords

import time

from gensim.test.utils import get_tmpfile

import gensim

#model.save(fname)
#model = Doc2Vec.load(fname)  # you can continue training with the loaded model!


In [3]:
ALL_FILES_LIST

['datasets/stackexchange/QueryResults 20200301-20200620_1.csv',
 'datasets/stackexchange/QueryResults 20200301-20200620_6.csv',
 'datasets/stackexchange/QueryResults 20200301-20200620_2.csv',
 'datasets/stackexchange/QueryResults 20200301-20200620_5.csv',
 'datasets/stackexchange/QueryResults 20200301-20200620_4.csv',
 'datasets/stackexchange/QueryResults 20200301-20200620_3.csv']

# Load data

In [4]:
import pandas as pd

pd.set_option('display.max_columns', None)

feats_list = ['Title', 'Body', 'Tags']

def load_data(data_path=DATA_PATH):
    csv_path = DATA_PATH_FILE
    df_list = []
    
    for f in ALL_FILES_LIST:
        print(f'Loading file {f}')
        
        df_list.append(pd.read_csv(f, sep=',', header=0, encoding='utf-8', usecols=feats_list))
        
    return pd.concat(df_list)


In [5]:
df = load_data()
df.reset_index(inplace=True)

Loading file datasets/stackexchange/QueryResults 20200301-20200620_1.csv
Loading file datasets/stackexchange/QueryResults 20200301-20200620_6.csv
Loading file datasets/stackexchange/QueryResults 20200301-20200620_2.csv
Loading file datasets/stackexchange/QueryResults 20200301-20200620_5.csv
Loading file datasets/stackexchange/QueryResults 20200301-20200620_4.csv
Loading file datasets/stackexchange/QueryResults 20200301-20200620_3.csv


In [6]:
df

index                                               Body  \
0           0  <p>Will a <code>StreamBuilder</code> always st...   
1           1  <p>The problem was not the filtering - I was a...   
2           2  <p>My two cents:</p>\n\n<p>You can specify the...   
3           3  <p>if you want to step up from that manual con...   
4           4  <p>The parent function is already asynchronous...   
...       ...                                                ...   
299995  49995  <p>I wanted to use turicreate library which do...   
299996  49996  <p>Please make sure there are only 'male' &amp...   
299997  49997  <p>Either use <code>android:requestLegacyExter...   
299998  49998  <p>I have a messagedialog to update after some...   
299999  49999  <p>I still miss some information to give you a...   

                                                    Title  \
0       Does StreamBuilder always listen in the first ...   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                                   ...   
299995   How can I effectively downgrade python in Linux?   
299996                                                NaN   
299997                                                NaN   
299998                             MessageBox freezes GTK   
299999                                                NaN   

                                               Tags  
0                                         <flutter>  
1                                               NaN  
2                                               NaN  
3                                               NaN  
4                                               NaN  
...                                             ...  
299995  <python><python-3.x><linux><pip><archlinux>  
299996                                          NaN  
299997                                          NaN  
299998                   <python><python-3.x><gtk3>  
299999                                          NaN  

[300000 rows x 4 columns]

## Drop NA and Remove html tags

In [8]:
df.dropna(subset=['Body'], axis=0, inplace=True)

In [9]:
# Or with beautifulsoup
df.loc[:, 'Body'] = df['Body'].apply(lambda x: BeautifulSoup(x, 'lxml').get_text())

In [10]:
df

index                                               Body  \
0           0  Will a StreamBuilder always start listening to...   
1           1  The problem was not the filtering - I was acce...   
2           2  My two cents:\nYou can specify the start time ...   
3           3  if you want to step up from that manual config...   
4           4  The parent function is already asynchronous, s...   
...       ...                                                ...   
299995  49995  I wanted to use turicreate library which doesn...   
299996  49996  Please make sure there are only 'male' & 'fema...   
299997  49997  Either use android:requestLegacyExternalStorag...   
299998  49998  I have a messagedialog to update after some de...   
299999  49999  I still miss some information to give you a sp...   

                                                    Title  \
0       Does StreamBuilder always listen in the first ...   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                                   ...   
299995   How can I effectively downgrade python in Linux?   
299996                                                NaN   
299997                                                NaN   
299998                             MessageBox freezes GTK   
299999                                                NaN   

                                               Tags  
0                                         <flutter>  
1                                               NaN  
2                                               NaN  
3                                               NaN  
4                                               NaN  
...                                             ...  
299995  <python><python-3.x><linux><pip><archlinux>  
299996                                          NaN  
299997                                          NaN  
299998                   <python><python-3.x><gtk3>  
299999                                          NaN  

[299920 rows x 4 columns]

In [12]:
# Converting tags from <tag 1><tag2><tag3> to tag1 tag2 tag3
df.loc[:, 'Tags'] = df['Tags'].str.replace('<', '') 
df.loc[:, 'Tags'] = df.loc[:, 'Tags'].str.replace('>', ' ') 
df.loc[:, 'Tags'] = df.loc[:, 'Tags'].str.rstrip()

In [13]:
df

index                                               Body  \
0           0  Will a StreamBuilder always start listening to...   
1           1  The problem was not the filtering - I was acce...   
2           2  My two cents:\nYou can specify the start time ...   
3           3  if you want to step up from that manual config...   
4           4  The parent function is already asynchronous, s...   
...       ...                                                ...   
299995  49995  I wanted to use turicreate library which doesn...   
299996  49996  Please make sure there are only 'male' & 'fema...   
299997  49997  Either use android:requestLegacyExternalStorag...   
299998  49998  I have a messagedialog to update after some de...   
299999  49999  I still miss some information to give you a sp...   

                                                    Title  \
0       Does StreamBuilder always listen in the first ...   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                                   ...   
299995   How can I effectively downgrade python in Linux?   
299996                                                NaN   
299997                                                NaN   
299998                             MessageBox freezes GTK   
299999                                                NaN   

                                         Tags  
0                                     flutter  
1                                         NaN  
2                                         NaN  
3                                         NaN  
4                                         NaN  
...                                       ...  
299995  python python-3.x linux pip archlinux  
299996                                    NaN  
299997                                    NaN  
299998                 python python-3.x gtk3  
299999                                    NaN  

[299920 rows x 4 columns]

In [14]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 299920 entries, 0 to 299999
Data columns (total 4 columns):
 #   Column  Non-Null Count   Dtype 
---  ------  --------------   ----- 
 0   index   299920 non-null  int64 
 1   Body    299920 non-null  object
 2   Title   149323 non-null  object
 3   Tags    149323 non-null  object
dtypes: int64(1), object(3)
memory usage: 11.4+ MB


In [15]:
df.sample(100)

index                                               Body  \
173039  23039  I want to write a test for my intellij idea pl...   
35511   35511  I have to a pyspark dataframe\ndf1.show()\n+--...   
285631  35631  Thx for the idea @AcsErno. With this I figured...   
229863  29863  I have created a new custom post type and crea...   
99031   49031  Welcome to SO ! \nFirst , have a check with To...   
164875  14875  Missing opening parenthesis after VALUES. Also...   
11896   11896  Op probably doesn't need the answer now but so...   
121254  21254  \n"What does int i do inside of the for loop?"...   
17431   17431  Here you go:\npublic static void main(String[]...   
222466  22466  Listview has onTap event which will give you p...   
126811  26811  SELECT LISTAGG(PRIME_NUMBER,'&') WITHIN GROUP ...   
246558  46558  use two while loops:\nt = 1;\nwhile t < M-1\n ...   
118336  18336  On running dig command:\ndig testdb.c7hgibdbsg...   
201721   1721  Flutter supports autofill now :) You may need ...   
253882   3882  Entity Framework Core uses what's called the "...   
282081  32081  I don't think there is any problem with the de...   
273056  23056  I want to create a replicaset of confiserver. ...   
47378   47378  I'm have an issue with compiling my program wi...   
186069  36069  I'm sending a request from a webpage :\n<scrip...   
228801  28801  Just properly quote the line and use different...   
23436   23436  If you are going to parse a language you need ...   
46689   46689  I have an image ~(5000*5000*8).I converted thi...   
86321   36321  I am running .net core 3.1 AWS Lambda function...   
213764  13764  I cannot find documentation anywhere regarding...   
98422   48422  Actually, it's not related to the dynamic impo...   
46502   46502  doctest.testmod()\n\nruns doctests in __main__...   
6485     6485  +------------+---------+----------+-----------...   
74381   24381  Lets say I have the following df:\nrs = np.ran...   
226626  26626  Update to 5.0.11, should resolve the issue\nfi...   
159859   9859  Try this, add\nprint(df1.set_index('date').add...   
64835   14835  I have the following avro definition for my Ni...   
40711   40711  I have trained a CNN network using dataset = t...   
170331  20331  var map = L.map("map").setView([51.505, -0.09]...   
218589  18589  you will need to import post_home:\nfrom djang...   
143689  43689  Good day All!\nI have been trying to convert J...   
616       616  You can do conditional aggregation. Assuming, ...   
215858  15858  The following demo uses array.map to render th...   
238764  38764  Assuming pip is already installed on your devi...   
204168   4168  \nI want to sign out the user in MainActivity....   
116268  16268  done() shouldn't be used in this case and the ...   
278615  28615  Another Potential Solution - Deploying Web Job...   
176667  26667  I have a 'front' page on www.host.com and a SP...   
126395  26395  I have set the Queue name and connection facto...   
109407   9407  We can use rleid from data.table\nlibrary(data...   
157696   7696  If you can get your date in milliseconds than ...   
4069     4069  In switch statement, the value of the expressi...   
95133   45133  if you do not change the privacy settings,\nth...   
171328  21328  I have a simple python/flask api that I am una...   
72166   22166  I'm trying to use Crispy Forms in my template,...   
288367  38367  Is there a way to change the names of the colu...   
252637   2637  I work on an app with iOS and Android versions...   
162745  12745  I am using a submodule in one of my CI jobs. B...   
117276  17276  The scheduler of the kernel running the contai...   
80520   30520  So i have written a program that reads a .obj ...   
106208   6208  Is it possible that you need to return your fu...   
246399  46399  In dash >= 1.11.0 you may use Pattern-Matching...   
274745  24745  I have made a Measurements model which has a f...   
121767  21767  I had installed ruby by \nrvm upgrade 2.7.1\n\...

In [16]:
df

index                                               Body  \
0           0  Will a StreamBuilder always start listening to...   
1           1  The problem was not the filtering - I was acce...   
2           2  My two cents:\nYou can specify the start time ...   
3           3  if you want to step up from that manual config...   
4           4  The parent function is already asynchronous, s...   
...       ...                                                ...   
299995  49995  I wanted to use turicreate library which doesn...   
299996  49996  Please make sure there are only 'male' & 'fema...   
299997  49997  Either use android:requestLegacyExternalStorag...   
299998  49998  I have a messagedialog to update after some de...   
299999  49999  I still miss some information to give you a sp...   

                                                    Title  \
0       Does StreamBuilder always listen in the first ...   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                                   ...   
299995   How can I effectively downgrade python in Linux?   
299996                                                NaN   
299997                                                NaN   
299998                             MessageBox freezes GTK   
299999                                                NaN   

                                         Tags  
0                                     flutter  
1                                         NaN  
2                                         NaN  
3                                         NaN  
4                                         NaN  
...                                       ...  
299995  python python-3.x linux pip archlinux  
299996                                    NaN  
299997                                    NaN  
299998                 python python-3.x gtk3  
299999                                    NaN  

[299920 rows x 4 columns]

# Regroup text features and clean

In [17]:
df.loc[:, 'Title'].fillna(value='', inplace=True)

In [18]:
df['all_text'] = df['Title'].astype(str) + '. ' +  df['Body'].astype(str)

In [19]:
df['all_text']

0         Does StreamBuilder always listen in the first ...
1         . The problem was not the filtering - I was ac...
2         . My two cents:\nYou can specify the start tim...
3         . if you want to step up from that manual conf...
4         . The parent function is already asynchronous,...
                                ...                        
299995    How can I effectively downgrade python in Linu...
299996    . Please make sure there are only 'male' & 'fe...
299997    . Either use android:requestLegacyExternalStor...
299998    MessageBox freezes GTK. I have a messagedialog...
299999    . I still miss some information to give you a ...
Name: all_text, Length: 299920, dtype: object

# Split training set, test set

In [20]:
df, df_train, df_test = custom_train_test_split_sample(df, None)

In [21]:
df_train.reset_index(drop=True, inplace=True)

In [22]:
df_train

index                                               Body  \
0       29281  I'm using Vividus to test my application.\nHow...   
1       34687  Answer relates to comment https://stackoverflo...   
2       43417  I'm trying to add a table (VDS) column and des...   
3        7005  You may need to create a state machine, where ...   
4       28129  I think you can use ternary operator\n${(var =...   
...       ...                                                ...   
269923  19908  When you give an input, even if it is a charac...   
269924   9245  I am not sure I am fully clear on the spec but...   
269925  31971  You correctly choosed recursive CTE. Unfortuna...   
269926  46909  Basically you are looking to add options to se...   
269927  21991  if you are using StoryBoard uncheck Show Horiz...   

                                                    Title  \
0         How to test downloading files with Vividus tool   
1                                                           
2       Adding Table column and column descriptions fo...   
3                                                           
4                                                           
...                                                   ...   
269923                                                      
269924                                                      
269925                                                      
269926                                                      
269927                                                      

                                    Tags  \
0       automation ui-automation vividus   
1                                    NaN   
2                            wiki dremio   
3                                    NaN   
4                                    NaN   
...                                  ...   
269923                               NaN   
269924                               NaN   
269925                               NaN   
269926                               NaN   
269927                               NaN   

                                                 all_text  
0       How to test downloading files with Vividus too...  
1       . Answer relates to comment https://stackoverf...  
2       Adding Table column and column descriptions fo...  
3       . You may need to create a state machine, wher...  
4       . I think you can use ternary operator\n${(var...  
...                                                   ...  
269923  . When you give an input, even if it is a char...  
269924  . I am not sure I am fully clear on the spec b...  
269925  . You correctly choosed recursive CTE. Unfortu...  
269926  . Basically you are looking to add options to ...  
269927  . if you are using StoryBoard uncheck Show Hor...  

[269928 rows x 5 columns]

In [23]:
df_test.reset_index(drop=True, inplace=True)

In [24]:
df_train_ori = df_train.copy(deep=True)
df_test_ori = df_test.copy(deep=True)

# Doc2Vec training

In [29]:
cnt_label = 0
InputDocs = []
for document in df_train['all_text']:  # TO DO : relaunch this training with df_train
    #InputDocs.append(TaggedDocument(document,[cnt_label]))
    
    doc_transformed = remove_stopwords(document)
    doc_toappend = gensim.utils.simple_preprocess(doc_transformed)
    
    InputDocs.append(TaggedDocument(doc_toappend,[cnt_label]))    
    cnt_label += 1

In [26]:
InputDocs

[TaggedDocument(words=['how', 'to', 'test', 'downloading', 'files', 'with', 'vividus', 'tool', 'using', 'vividus', 'to', 'test', 'my', 'application', 'how', 'can', 'test', 'the', 'file', 'was', 'downloaded', 'after', 'click', 'on', 'the', 'download', 'button'], tags=[0]),
 TaggedDocument(words=['answer', 'relates', 'to', 'comment', 'https', 'stackoverflow', 'com', 'questions', 'logs', 'are', 'not', 'loading', 'according', 'to', 'log', 'properties', 'noredirect', 'comment', 'works', 'here', 'spring', 'boot', 'release', 'info', 'main', 'com', 'example', 'testlog', 'logstarting', 'org', 'springframework', 'boot', 'logstarting', 'java', 'starting', 'on', 'laptop', 'vihojt', 'with', 'pid', 'development', 'algaworks', 'workspace', 'test', 'log', 'target', 'classes', 'started', 'by', 'joaozarate', 'in', 'development', 'algaworks', 'workspace', 'test', 'log', 'info', 'main', 'com', 'example', 'testlog', 'org', 'springframework', 'boot', 'java', 'no', 'active', 'profile', 'set', 'falling', 'bac

In [30]:
InputDocs

[TaggedDocument(words=['how', 'test', 'downloading', 'files', 'vividus', 'tool', 'vividus', 'test', 'application', 'how', 'test', 'file', 'downloaded', 'click', 'download', 'button'], tags=[0]),
 TaggedDocument(words=['answer', 'relates', 'comment', 'https', 'stackoverflow', 'com', 'questions', 'logs', 'are', 'not', 'loading', 'according', 'to', 'log', 'properties', 'noredirect', 'comment', 'works', 'here', 'spring', 'boot', 'release', 'info', 'main', 'com', 'example', 'testlog', 'logstarting', 'org', 'springframework', 'boot', 'logstarting', 'java', 'starting', 'laptop', 'vihojt', 'pid', 'development', 'algaworks', 'workspace', 'test', 'log', 'target', 'classes', 'started', 'joaozarate', 'development', 'algaworks', 'workspace', 'test', 'log', 'info', 'main', 'com', 'example', 'testlog', 'org', 'springframework', 'boot', 'java', 'no', 'active', 'profile', 'set', 'falling', 'default', 'profiles', 'default', 'info', 'main', 'org', 'springframework', 'boot', 'web', 'embedded', 'tomcat', '

In [83]:
start = time.time()
model_doc2vec = Doc2Vec(InputDocs, vector_size=200, window=5, min_count=5, workers=4)  # All input docs loaded in memory
end = time.time()

print('Durée doc2vec training: ' + str(end - start) + ' secondes')    

Durée doc2vec training: 390.84519720077515 secondes


In [84]:
#model_doc2vec.save(doc2vec_fname)
model_doc2vec.save(DOC2VEC_TRAINING_SAVE_FILE)

In [81]:
TaggedDocument(gensim.utils.simple_preprocess(df_train.iloc[0]['all_text']), [0])

TaggedDocument(words=['how', 'to', 'test', 'downloading', 'files', 'with', 'vividus', 'tool', 'using', 'vividus', 'to', 'test', 'my', 'application', 'how', 'can', 'test', 'the', 'file', 'was', 'downloaded', 'after', 'click', 'on', 'the', 'download', 'button'], tags=[0])

In [86]:
gensim.utils.simple_preprocess("Hello this is a new text")

['hello', 'this', 'is', 'new', 'text']

In [91]:
[model_doc2vec.infer_vector(gensim.utils.simple_preprocess(text)) for text in ['hello this is', 'second text']]

[array([-0.01184898,  0.03453974,  0.06482397, -0.0286039 ,  0.02387763,
        -0.02638115,  0.02154115, -0.01048133, -0.02431484,  0.01125829,
         0.04940461, -0.00433267, -0.02208562,  0.00414025,  0.00503135,
        -0.02072092,  0.04314127, -0.03572913,  0.03535321,  0.02542022,
        -0.00624327,  0.02394359,  0.03502951,  0.01706566, -0.01901504,
        -0.00309338, -0.0010457 , -0.02870183, -0.01301771,  0.02158045,
        -0.00097381,  0.00093952, -0.04117129,  0.02662507,  0.0136477 ,
         0.01120851,  0.02996467, -0.00419346, -0.0103217 ,  0.00551189,
         0.05406   , -0.03664529, -0.00318097,  0.00919047, -0.00512499,
         0.01477685, -0.02402533, -0.04493537, -0.00560615, -0.00380771,
         0.04191558, -0.00592381, -0.03236176, -0.00669206,  0.011272  ,
        -0.02250443,  0.01086957, -0.00241925,  0.02183758, -0.04547973,
         0.00897735,  0.013061  , -0.04226149, -0.03725126, -0.03595147,
         0.00102091, -0.00271897, -0.00432519,  0.0

In [27]:
df_train.shape

(269928, 5)

In [44]:
df_train.iloc[0]

index                                                   29281
Body        I'm using Vividus to test my application.\n\nH...
Title         How to test downloading files with Vividus tool
Tags                         automation ui-automation vividus
all_text    How to test downloading files with Vividus too...
Name: 179281, dtype: object

In [40]:
df_train.loc[:5,'all_text']

179281    How to test downloading files with Vividus too...
284687    . Answer relates to comment https://stackoverf...
293417    Adding Table column and column descriptions fo...
57005     . You may need to create a state machine, wher...
128129    . I think you can use ternary operator\n${(var...
                                ...                        
278698    -bash: node: command not found. A complete noo...
268629    . Python keeps track of how many references a ...
269253    . You could try this ( this was inspired by @j...
234211    . Go to the Form1.cs hold ctrl and press on th...
5         . It is not that easy to detect restrict viola...
Name: all_text, Length: 258290, dtype: object

In [49]:
a = [document for document in df_train.loc[:,'all_text'] ]

In [51]:
df_train.shape

(269928, 5)

In [50]:
len(a)

269928

In [54]:
X_vectorized = [model_doc2vec.infer_vector(TaggedDocument(document)) for document in df_train.loc[:, 'all_text']]

TypeError: __new__() missing 1 required positional argument: 'tags'

In [33]:
X_vectorized

array([ 1.7391864e-03, -2.4041089e-03, -6.1061885e-04, -6.9943938e-04,
       -1.2304492e-03,  2.1471009e-03,  6.3857110e-04,  1.8232190e-03,
       -2.1374806e-05,  2.0389820e-03,  1.8796850e-03, -8.5410784e-04,
       -1.2674469e-04,  5.4166600e-04, -2.3427752e-03, -1.9247407e-03,
       -1.4666322e-03,  1.7130738e-03, -2.0551239e-03, -2.1125069e-03,
       -4.8165154e-04, -2.3405398e-03,  2.2211964e-03, -2.7337202e-04,
        1.8088296e-03, -2.1811242e-03, -7.5851125e-04, -1.3131672e-03,
        8.2151504e-04, -1.0208723e-03,  1.2520794e-03,  3.1241972e-05,
        1.4360896e-03,  4.8982719e-04,  2.6912722e-04,  1.7474059e-03,
       -2.0627065e-03, -8.0414327e-05, -4.0863961e-04, -7.2816346e-04,
        2.3532470e-03, -1.9800293e-03,  7.5416558e-04,  1.8871014e-03,
        8.6456462e-04,  1.1529382e-03, -2.4339389e-03, -7.9831557e-04,
       -9.8235765e-04,  1.8281783e-03,  1.1675517e-03,  1.1204255e-03,
        2.0028462e-03,  4.4137498e-04, -1.5815584e-03,  2.0862177e-03,
      

# Doc2vec loading

In [35]:
df

index                                               Body  \
0           0  Will a StreamBuilder always start listening to...   
1           1  The problem was not the filtering - I was acce...   
2           2  My two cents:\nYou can specify the start time ...   
3           3  if you want to step up from that manual config...   
4           4  The parent function is already asynchronous, s...   
...       ...                                                ...   
299995  49995  I wanted to use turicreate library which doesn...   
299996  49996  Please make sure there are only 'male' & 'fema...   
299997  49997  Either use android:requestLegacyExternalStorag...   
299998  49998  I have a messagedialog to update after some de...   
299999  49999  I still miss some information to give you a sp...   

                                                    Title  \
0       Does StreamBuilder always listen in the first ...   
1                                                           
2                                                           
3                                                           
4                                                           
...                                                   ...   
299995   How can I effectively downgrade python in Linux?   
299996                                                      
299997                                                      
299998                             MessageBox freezes GTK   
299999                                                      

                                         Tags  \
0                                     flutter   
1                                         NaN   
2                                         NaN   
3                                         NaN   
4                                         NaN   
...                                       ...   
299995  python python-3.x linux pip archlinux   
299996                                    NaN   
299997                                    NaN   
299998                 python python-3.x gtk3   
299999                                    NaN   

                                                 all_text  
0       Does StreamBuilder always listen in the first ...  
1       . The problem was not the filtering - I was ac...  
2       . My two cents:\nYou can specify the start tim...  
3       . if you want to step up from that manual conf...  
4       . The parent function is already asynchronous,...  
...                                                   ...  
299995  How can I effectively downgrade python in Linu...  
299996  . Please make sure there are only 'male' & 'fe...  
299997  . Either use android:requestLegacyExternalStor...  
299998  MessageBox freezes GTK. I have a messagedialog...  
299999  . I still miss some information to give you a ...  

[299920 rows x 5 columns]

In [55]:
from functions import *
importlib.reload(sys.modules['functions'])

<module 'functions' from '/home/francois/coding/OC/PJ6/functions.py'>

In [57]:
doc2vec = Doc2Vec_Vectorizer(model_path=DOC2VEC_TRAINING_SAVE_FILE, feature_totransform='all_text')

In [64]:
df_train_transformed = doc2vec.transform(df_train)

In [65]:
df_train_transformed

[array([-0.05801707,  0.07423116,  0.2965036 , -0.07720322,  0.15802228,
        -0.05075034,  0.05026644, -0.02154841, -0.06259517,  0.01072377,
         0.1164235 ,  0.06252893, -0.02486542,  0.01956156, -0.04199762,
        -0.11311964,  0.11637112, -0.10089996,  0.13848323,  0.09863374,
        -0.05830193,  0.05675882,  0.0701333 , -0.00187582, -0.10792606,
        -0.08736826,  0.02979787,  0.03808298, -0.01168508,  0.07564363,
         0.04557799,  0.04201014, -0.10883784,  0.08780699, -0.00511123,
         0.08950495,  0.14183667, -0.0174731 ,  0.11603991, -0.02252715,
         0.08633002, -0.12111788,  0.02258534, -0.00975577,  0.03713678,
         0.04643444,  0.00521989, -0.07777736, -0.11414106,  0.09445088,
         0.12391072,  0.03162298, -0.11809427,  0.03730294,  0.01560557,
        -0.06989601,  0.0692184 , -0.06706607,  0.12831561, -0.15606938,
         0.01967131,  0.03045373, -0.03695109, -0.00977936, -0.03005865,
         0.01466672, -0.18482694, -0.05308868, -0.0